In [7]:
#import sys
#print(sys.executable)


/home/ubuntu/.local/share/pipx/venvs/notebook/bin/python


In [10]:
#!{sys.executable} -m pip install pandas numpy scikit-learn matplotlib seaborn


  Using cached pandas-2.2.3-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (89 kB)
  Using cached numpy-2.1.3-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (62 kB)
  Using cached scikit_learn-1.5.2-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (13 kB)
  Using cached matplotlib-3.9.2-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (11 kB)
  Using cached pytz-2024.2-py2.py3-none-any.whl.metadata (22 kB)
  Using cached tzdata-2024.2-py2.py3-none-any.whl.metadata (1.4 kB)
  Using cached scipy-1.14.1-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (60 kB)
  Using cached joblib-1.4.2-py3-none-any.whl.metadata (5.4 kB)
  Using cached threadpoolctl-3.5.0-py3-none-any.whl.metadata (13 kB)
  Using cached contourpy-1.3.1-cp312-cp312-manylinux_2_17_x86_64.manylinux2014_x86_64.whl.metadata (5.4 kB)
  Using cached cycler-0.12.1-py3-none-any.whl.metadata (3.8 kB)
  Using cached fonttools-4.54.1-cp

In [3]:
import pandas as pd
import numpy as np
from sklearn.metrics.pairwise import cosine_similarity
from sklearn.manifold import TSNE
import matplotlib.pyplot as plt
import seaborn as sns
import os

In [4]:
def create_folders_if_not_exists(folders):
  for path in folders:
    if not os.path.exists(path):
      os.makedirs(path)


In [5]:
precision = 'allele'
pipeline_data = './data_10x'
pipeline_data_plain = f'{pipeline_data}/plain_datasets'
pipeline_data_cleaned = f'{pipeline_data}/cleaned_datasets'
pipeline_data_concatenated = f'{pipeline_data}/concatenated_datasets'
pipeline_data_splitted = f'{pipeline_data}/splitted_datasets'
pipeline_data_temp_bucket = f'{pipeline_data}/temp'

pipeline_folders = [pipeline_data, pipeline_data_plain, pipeline_data_cleaned, pipeline_data_concatenated, pipeline_data_splitted, pipeline_data_temp_bucket]

create_folders_if_not_exists(pipeline_folders)

In [6]:
# Laden von Embeddings für die "paired" Daten
tra_embeddings = np.load(f"{pipeline_data}/embeddings/paired/{precision}/TRA_paired_embeddings.npz")
trb_embeddings = np.load(f"{pipeline_data}/embeddings/paired/{precision}/TRB_paired_embeddings.npz")
epitope_embeddings = np.load(f"{pipeline_data}/embeddings/paired/{precision}/Epitope_paired_embeddings.npz")

In [ ]:
# Anzeigen der Schlüssel in jeder Datei
print("Keys in TRA Embeddings:", tra_embeddings.keys())
print("Keys in TRB Embeddings:", trb_embeddings.keys())
print("Keys in Epitope Embeddings:", epitope_embeddings.keys())

# Die ersten 5 Zeilen der Werte für jeden Schlüssel anzeigen (beispielsweise für den ersten Schlüssel)
# Ersetzen Sie 'key_name' durch den tatsächlichen Namen eines Schlüssels in den Embeddings
for key in tra_embeddings.keys():
    print(f"\nFirst 5 rows for {key} in TRA Embeddings:")
    print(tra_embeddings[key][:5])

for key in trb_embeddings.keys():
    print(f"\nFirst 5 rows for {key} in TRB Embeddings:")
    print(trb_embeddings[key][:5])

for key in epitope_embeddings.keys():
    print(f"\nFirst 5 rows for {key} in Epitope Embeddings:")
    print(epitope_embeddings[key][:5])

Keys in TRA Embeddings: KeysView(NpzFile './data_10x/embeddings/paired/allele/TRA_paired_embeddings.npz' with keys: CAVDGNQFYF, CATSAGNMLTF, CALEDGQKLLF, CIVYTGNQFYF, CAVRTGNQFYF...)
Keys in TRB Embeddings: KeysView(NpzFile './data_10x/embeddings/paired/allele/TRB_paired_embeddings.npz' with keys: CASSVAGSSYEQYF, CASSTGTGLREQYF, CASSLAELAGDKDTQYF, CAFLGCN**KLFF, CASTSIHVHNEQFF...)
Keys in Epitope Embeddings: KeysView(NpzFile './data_10x/embeddings/paired/allele/Epitope_paired_embeddings.npz' with keys: KIILFLALI, EIAGIGILTV, LMNVLTLFY, RLSDFSEQL, VLLGVKLSGV...)

First 5 rows for CAVDGNQFYF in TRA Embeddings:
[[ 0.00095297 -0.06201586 -0.1716909  ...  0.2522998   0.15069914
   0.01806563]
 [ 0.31839043 -0.1079285  -0.41729435 ...  0.06177479  0.03275375
   0.09239022]
 [ 0.07380157 -0.00857734 -0.40101543 ...  0.07367489  0.01422306
   0.15355338]
 [ 0.07178663 -0.01083522  0.05325813 ... -0.01112144 -0.01931327
   0.1721242 ]
 [ 0.26585364  0.04242921  0.05933102 ...  0.03474645  0.047

In [16]:
# Annahme: Extrahieren von positiven und negativen Embeddings (als Beispiel)
# Sie sollten Ihre eigenen Kriterien für positive und negative Embeddings definieren
positive_embeddings = tra_embeddings['positive_key']  # Ersetzen Sie 'positive_key' mit Ihrem tatsächlichen Schlüssel
negative_embeddings = tra_embeddings['negative_key']  # Ersetzen Sie 'negative_key' mit Ihrem tatsächlichen Schlüssel

# Falls erforderlich, Flatten der Embeddings
positive_embeddings = positive_embeddings.reshape(len(positive_embeddings), -1)
negative_embeddings = negative_embeddings.reshape(len(negative_embeddings), -1)

# Schritt 3: Berechne Cosinus-Similarity zwischen positiven und negativen Embeddings
similarity_matrix = cosine_similarity(positive_embeddings, negative_embeddings)

# Durchschnittliche Cosinus-Similarity berechnen
average_similarity = np.mean(similarity_matrix)
print(f"Durchschnittliche Cosinus-Similarity zwischen positiven und negativen Samples: {average_similarity}")

# Schritt 4: t-SNE für die Visualisierung
# Kombiniere Embeddings zur Visualisierung
all_embeddings = np.vstack([positive_embeddings, negative_embeddings])
labels = ['Positive'] * len(positive_embeddings) + ['Negative'] * len(negative_embeddings)

# t-SNE auf die Embeddings anwenden
tsne = TSNE(n_components=2, perplexity=30, random_state=42)
embeddings_2d = tsne.fit_transform(all_embeddings)

# Plot der Ergebnisse
plt.figure(figsize=(10, 7))
sns.scatterplot(x=embeddings_2d[:, 0], y=embeddings_2d[:, 1], hue=labels, palette=['blue', 'red'])
plt.title('t-SNE der Embeddings (Positive vs Negative)')
plt.xlabel('t-SNE Komponente 1')
plt.ylabel('t-SNE Komponente 2')
plt.legend(title='Sample Typ')
plt.show()

NameError: name 'positive_embeddings' is not defined